<a href="https://colab.research.google.com/github/rachelyayra/AIAssignment/blob/main/SEMEVAL_TABULAR_QA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Overview of Code Implementation

This notebook demonstrates the implementation of a question-answering system over tabular data using the TAPAS and T5 models. The goal is to train a model that can effectively answer questions based on the context provided by structured tables.

## Key Components:

1. **Data Preparation**:
   - The dataset consists of tables that are structured for question-answering tasks.
   - The first 1,000 tables are selected for the training set, while the subsequent 300 tables are designated for validation.

2. **Model Initialization**:
   - Models are initialized using the appropriate architectures (TAPAS and GPT2) designed for processing tabular data and generating text-based responses.

3. **Training Loop**:
   - The training process includes:
     - is done with a sequence2sequence trainer

4. **Validation**:
   - A validation phase is integrated to assess the model's performance on unseen data after each epoch, ensuring that the model generalizes well.

5. **Error Handling**:
   - The implementation includes error handling to gracefully skip batches that encounter issues during processing.

6. **Batch Loss Tracking**:
   - The notebook maintains a list of batch losses, which can be analyzed after training to understand the model's learning behavior over time.


# HOUSE KEEPING

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install datasets

INFO: pip is looking at multiple versions of multiprocess to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 471.6/471.6 kB 33.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 17.9 MB/s eta 0:00:00


In [ ]:
import pandas as pd
from datasets import load_dataset
from transformers import TapasTokenizer, TapasForQuestionAnswering

import torch
import torch.nn as nn
from transformers import TapasModel, T5ForConditionalGeneration, T5Tokenizer
from torch.utils.data import DataLoader, Dataset
from transformers import AdamW
from transformers import TapasModel, T5ForConditionalGeneration, T5Tokenizer, AutoTokenizer, Seq2SeqTrainingArguments, Seq2SeqTrainer
from transformers import EncoderDecoderModel, T5Tokenizer, T5ForConditionalGeneration, TapasTokenizer, TapasForQuestionAnswering

# DATA

In [ ]:
# Load the QA pairs
semeval_dev_qa = load_dataset("cardiffnlp/databench", name="semeval", split="dev")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/43.6k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/65 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/49 [00:00<?, ?it/s]

qa.parquet:   0%|          | 0.00/7.74k [00:00<?, ?B/s]

...

qa.parquet:   0%|          | 0.00/8.23k [00:00<?, ?B/s]

qa.parquet:   0%|          | 0.00/9.46k [00:00<?, ?B/s]

qa.parquet:   0%|          | 0.00/7.46k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/988 [00:00<?, ? examples/s]

Generating dev split:   0%|          | 0/320 [00:00<?, ? examples/s]

In [ ]:
# Explore the data
print(semeval_dev_qa)


# Check the structure of the first dataset
print(semeval_dev_qa['dataset'][0])  # View the first QA pair

Dataset({
    features: ['question', 'answer', 'type', 'columns_used', 'column_types', 'sample_answer', 'dataset'],
    num_rows: 320
})
050_ING


In [ ]:
for i in semeval_dev_qa:
  print(f"Question: {i['question']}")
  print(f"Answer: {i['answer']}")
  print(f"Sample Answer: {i['sample_answer']}")
  print(f"Columns: {i['columns_used']}")
  print(f"Columns: {i['column_types']}")

Question: Is the most favorited author mainly communicating in Spanish?
Answer: True
Sample Answer: True
Columns: ['favorites', 'lang']
Columns: ['category', 'category']
Question: Does the author with the longest name post mainly original content?
Answer: True
Sample Answer: False
Columns: ['author_name', 'type']
Columns: ['category', 'category']
Question: Is there an author who received no retweets for any of their posts?
Answer: True
Sample Answer: True
Columns: ['author_name', 'retweets']
Columns: ['category', 'number[uint8]']
Question: Are there any posts that do not contain any links?
Answer: True
Sample Answer: True
Columns: ['links']
Columns: ['list[url]']
Question: How many unique authors are in the dataset?
Answer: 3765
Sample Answer: 20
Columns: ['author_name']
Columns: ['category']
Question: What is the length of the longest post (based on the number of words)?
Answer: 61
Sample Answer: 49
Columns: ['text']
Columns: ['text']
Question: What is the total number of retweets rec

# TRAINING

In [ ]:
# Load the TAPAS model and extract the encoder
from transformers import EncoderDecoderModel, TapasForQuestionAnswering, TapasTokenizer, GPT2LMHeadModel, GPT2Tokenizer
from transformers import EncoderDecoderModel, GPT2Config, TapasForQuestionAnswering, GPT2LMHeadModel

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
tapas_model = TapasModel.from_pretrained("google/tapas-base")
tapas_encoder = tapas_model.to(device)
tokenizer = AutoTokenizer.from_pretrained("google/tapas-base")
# Load the T5 model (decoder) and tokenizer

gpt2_tokenizer = GPT2Tokenizer.from_pretrained("gpt2")
config = GPT2Config.from_pretrained("gpt2", add_cross_attention=True)
gpt2_model = GPT2LMHeadModel.from_pretrained("gpt2", config=config)


config.json:   0%|          | 0.00/1.52k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/443M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/490 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/262k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/154 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

Some weights of GPT2LMHeadModel were not initialized from the model checkpoint at gpt2 and are newly initialized: ['h.0.crossattention.c_attn.bias', 'h.0.crossattention.c_attn.weight', 'h.0.crossattention.c_proj.bias', 'h.0.crossattention.c_proj.weight', 'h.0.crossattention.q_attn.bias', 'h.0.crossattention.q_attn.weight', 'h.0.ln_cross_attn.bias', 'h.0.ln_cross_attn.weight', 'h.1.crossattention.c_attn.bias', 'h.1.crossattention.c_attn.weight', 'h.1.crossattention.c_proj.bias', 'h.1.crossattention.c_proj.weight', 'h.1.crossattention.q_attn.bias', 'h.1.crossattention.q_attn.weight', 'h.1.ln_cross_attn.bias', 'h.1.ln_cross_attn.weight', 'h.10.crossattention.c_attn.bias', 'h.10.crossattention.c_attn.weight', 'h.10.crossattention.c_proj.bias', 'h.10.crossattention.c_proj.weight', 'h.10.crossattention.q_attn.bias', 'h.10.crossattention.q_attn.weight', 'h.10.ln_cross_attn.bias', 'h.10.ln_cross_attn.weight', 'h.11.crossattention.c_attn.bias', 'h.11.crossattention.c_attn.weight', 'h.11.crossat

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

In [ ]:
# model = EncoderDecoderModel(encoder=tapas_model, decoder=gpt2_model)
model = torch.load('/content/drive/MyDrive/model_complete.pth')

<ipython-input-7-39812beaa007>:2: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model = torch.load('/content/drive/MyDrive/model_complete.pth')


In [ ]:
import os
import shutil
import pandas as pd
import torch
from transformers import  TapasForQuestionAnswering
from IPython.display import display, HTML


# Convert table to tokenizer-friendly format
def convert_table_to_inputs(table_data, queries):
    table = pd.DataFrame(table_data.values.tolist(), columns=table_data.columns)
    table = table.map(str)

    # Tokenize the inputs using the Tapas tokenizer
    inputs = tokenizer(
        table=table,
        queries=queries,
        padding="max_length",
        max_length = 512,
        truncation=True,
        return_tensors="pt"
    )

    inputs = {key: value.to(device) for key, value in inputs.items()}

    return inputs, table

In [ ]:
all_qa = load_dataset("cardiffnlp/databench", name="qa", split="train").to_pandas()

# Define a custom dataset
# Define a custom dataset
class TabularQADataset(Dataset):
    def __init__(self, qa_data):
        self.qa_data = qa_data

    def __len__(self):
        return len(self.qa_data)

    def __getitem__(self, idx):

        question = self.qa_data.loc[idx, 'question']
        dataset_id = self.qa_data.loc[idx, 'dataset']

        # Load the corresponding table
        df = pd.read_parquet(f"hf://datasets/cardiffnlp/databench/data/{dataset_id}/sample.parquet").head(250)

        # Convert the table to a list of lists or a format suitable for your model
        # Here, we concatenate all rows into a string or can directly use DataFrame for processing
        inputs, table = convert_table_to_inputs(df, str(question))


        # Prepare the answer (assuming the answer is in the 'answer' field)
        answer = self.qa_data.loc[idx, 'answer']
        if answer == None:
          answer = 'None'
        # Tokenize the answer using the T5 tokenizer
        print(f"Answer: {answer}")
        gpt2_tokenizer.pad_token = gpt2_tokenizer.eos_token

        target = gpt2_tokenizer(answer, padding='max_length', truncation=True, return_tensors="pt", max_length=32)

        target = {key: value.to(device) for key, value in target.items()}
        decoder_input_ids = torch.cat([torch.tensor([[gpt2_tokenizer.pad_token_id]]).to(device), target['input_ids'][:, :-1]], dim=1)

        # Return a dictionary
        return {'input_ids': inputs['input_ids'].squeeze(0),
                'attention_mask': inputs['attention_mask'].squeeze(0),
                'decoder_input_ids': decoder_input_ids.squeeze(),
                'labels': target['input_ids'].squeeze().long(),
                'decoder_attention_mask': target['attention_mask'].squeeze().long()}


# Create dataset and dataloader
dataset = TabularQADataset(all_qa[:1200].reset_index())
dataloader = DataLoader(dataset, batch_size=16, shuffle=True)  # Adjust batch size as needed

val_dataset = TabularQADataset(all_qa[1000:].reset_index())
val_dataloader = DataLoader(dataset, batch_size=32, shuffle=True)

Resolving data files:   0%|          | 0/65 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/65 [00:00<?, ?it/s]

Generating train split:   0%|          | 0/1308 [00:00<?, ? examples/s]

In [ ]:
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments

# # Define training arguments
# training_args = Seq2SeqTrainingArguments(
#     output_dir='./results',
#     evaluation_strategy='steps',
#     per_device_train_batch_size=16,
#     per_device_eval_batch_size=16,
#     logging_dir='./logs',
#     logging_steps=10,
#     num_train_epochs=2.1,
# )

# # Define the datasets
# train_dataset = dataset
# eval_dataset = val_dataset

# # Set up the Seq2SeqTrainer
# trainer = Seq2SeqTrainer(
#     model=model,
#     args=training_args,
#     train_dataset=train_dataset,
#     eval_dataset=eval_dataset,
#     tokenizer=tokenizer,  # Use TAPAS tokenizer
# )

# # Train the model
# trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]


Answer: [1.0, 2.0, 2.0, 2.0, 2.0]


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]


Answer: [26.0, 25.0]


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]


...

Answer: 20


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]


Answer: 504


/usr/local/lib/python3.10/dist-packages/transformers/models/encoder_decoder/modeling_encoder_decoder.py:643: FutureWarning: Version v4.12.0 introduces a better way to train encoder-decoder models by computing the loss inside the encoder-decoder framework rather than in the decoder itself. You may observe training discrepancies if fine-tuning a model trained with versions anterior to 4.12.0. The decoder_input_ids are now created based on the labels, no need to pass them yourself anymore.
  warnings.warn(DEPRECATION_WARNING, FutureWarning)


TrainOutput(global_step=158, training_loss=1.0431885266605812, metrics={'train_runtime': 9294.71, 'train_samples_per_second': 0.271, 'train_steps_per_second': 0.017, 'total_flos': 1545976456151040.0, 'train_loss': 1.0431885266605812, 'epoch': 2.1066666666666665})

In [ ]:
from transformers import AutoTokenizer, TapasForQuestionAnswering
import pandas as pd

# Prepare input data
question = all_qa.loc[1, 'question']
table_key = all_qa.loc[1, 'dataset']  # Get the dataset associated with the question

df = pd.read_parquet(f"hf://datasets/cardiffnlp/databench/data/{table_key}/all.parquet").head(250)

queries = question

inputs, table = convert_table_to_inputs(df, str(queries))


generated_ids = model.generate(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'])

# Decode the generated sequence
decoded_output = gpt2_tokenizer.decode(generated_ids[0], skip_special_tokens=True)
print(decoded_output)

/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `ma

[0.0, 0.0, 0.0, 0.0, 0.


In [ ]:
# torch.save(model, '/content/drive/MyDrive/model_complete.pth')

## The model successfully generates and answer

In [ ]:
def generate_predictions(qa_dataset, max_rows=100):
    predictions = []

    for idx, row in enumerate(qa_dataset):
        print(f"Row Number: {idx}")
        question = all_qa.loc[idx, 'question']
        table_key = all_qa.loc[idx, 'dataset']  # Get the dataset associated with the question

        df = pd.read_parquet(f"hf://datasets/cardiffnlp/databench/data/{table_key}/all.parquet").head(250)

        queries = question

        inputs, table = convert_table_to_inputs(df, str(queries))


        generated_ids = model.generate(input_ids=inputs['input_ids'], attention_mask=inputs['attention_mask'])

        # Decode the generated sequence
        decoded_output = gpt2_tokenizer.decode(generated_ids[0], skip_special_tokens=True)
        predictions.append(decoded_output)

    return predictions


In [ ]:
def generate_predictions_sample(qa_dataset, max_rows=100):
    predictions = []
    for idx, row in enumerate(qa_dataset):
        print(f"Row Number: {idx}")
        question = all_qa.loc[idx, 'question']
        table_key = all_qa.loc[idx, 'dataset']  # Get the dataset associated with the question

        df = pd.read_parquet(f"hf://datasets/cardiffnlp/databench/data/{table_key}/sample.parquet").head(250)

        queries = question

        inputs, table = convert_table_to_inputs(df, str(queries))


        generated_ids = model.generate(input_ids=inputs['input_ids'])

        # Decode the generated sequence
        decoded_output = gpt2_tokenizer.decode(generated_ids[0], skip_special_tokens=True)
        predictions.append(decoded_output)

    return predictions

### SAVE FILES

In [ ]:
predictions = generate_predictions(semeval_dev_qa)

Row Number: 0


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `ma

Row Number: 1


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `ma

Row Number: 2


...

/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `ma

Row Number: 318


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)
/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:1472: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  cell = row[col_index]
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1258: UserWarning: Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `ma

Row Number: 319


/usr/local/lib/python3.10/dist-packages/transformers/models/tapas/tokenization_tapas.py:2673: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  text = normalize_for_match(row[col_index].text)


In [ ]:
predictions_lite = generate_predictions_sample(semeval_dev_qa)

In [ ]:
with open('predictions_lite.txt', 'w') as f:
  for prediction in predictions:
    if len(prediction) < 1:
      prediction = 'False'
    f.write(f"{prediction}\n")  # Write each prediction on a new line

In [ ]:
with open('predictions.txt', 'w') as f:
  for prediction in predictions:
    if len(prediction) < 1:
      prediction = 'False'
    f.write(f"{prediction}\n")  # Write each prediction on a new line

In [ ]:
with zipfile.ZipFile("Archive.zip", "w") as zipf:
    zipf.write("predictions.txt")
    zipf.write("predictions_lite.txt")

print("Created Archive.zip containing predictions.txt and predictions_lite.txt")